In [44]:
import glob
import json
from datasets import Dataset


In [24]:
!free -h

               total        used        free      shared  buff/cache   available
Mem:           216Gi        16Gi       187Gi        87Mi        12Gi       197Gi
Swap:             0B          0B          0B


In [57]:


news_dataset = glob.glob("/home/ubuntu/Datasets/Raw_Datasets/news/*")

for x in glob.glob("/home/ubuntu/Datasets/Raw_Datasets/news/*"):
    print(x)

/home/ubuntu/Datasets/Raw_Datasets/news/therakyatpost.com.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/sinar_harian_link_politik.json
/home/ubuntu/Datasets/Raw_Datasets/news/selangorkini.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/utusan-20230512.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/theedgemalaysia.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/themalaysianinsights.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/malaysiakini-bm.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/kosmo-20230524.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/parse-bernama.json
/home/ubuntu/Datasets/Raw_Datasets/news/sinar_harian_link_sukan.json
/home/ubuntu/Datasets/Raw_Datasets/news/melakahariini.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/fmt.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/theborneopost.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/sinar_harian_link_berita.json
/home/ubuntu/Datasets/Raw_Datasets/news/malaymail-02.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/malaymail-01.jsonl
/home/

In [58]:
!du -sh /home/ubuntu/Datasets/Raw_Datasets/news

6.8G	/home/ubuntu/Datasets/Raw_Datasets/news


In [25]:
!df -h

Filesystem      Size  Used Avail Use% Mounted on
overlay         124G   27G   98G  22% /
tmpfs            64M     0   64M   0% /dev
/dev/sdc        492G  387G  106G  79% /home/ubuntu
/dev/root       124G   27G   98G  22% /etc/hosts
shm              64M   16K   64M   1% /dev/shm
tmpfs           205G   12K  205G   1% /run/secrets/kubernetes.io/serviceaccount
tmpfs           109G   12K  109G   1% /proc/driver/nvidia
tmpfs            44G   85M   44G   1% /run/nvidia-persistenced/socket
tmpfs           109G     0  109G   0% /proc/acpi
tmpfs           109G     0  109G   0% /proc/scsi
tmpfs           109G     0  109G   0% /sys/firmware


In [60]:
def process_json_file(file_path):
    
    keys = []
    data = []
    
    try:
        with open(file_path, 'r', encoding='utf-8') as f:
            file_content = f.read()
            try:
                data = json.loads(file_content)
                if data and isinstance(data, list) and len(data) > 0:
                    keys = [key for key in data[0].keys()]
            except json.JSONDecodeError:
                lines = file_content.split('\n')
                for line in lines:
                    if line.strip():
                        parsed_data = json.loads(line)
                        data.append(parsed_data)
                        if keys == []:
                            keys = [key for key in parsed_data.keys()]

    except Exception as e:
        print('error', e)
        
    return data, keys

def process_txt_file(file_path):
    with open(file_path, 'r', encoding='utf-8') as f:
        data = f.read()
    return data

In [61]:
keys = []
data = []


for filename in news_dataset:
    
    print(filename)
    
    if filename.endswith('.json'):
        content,key = process_json_file(filename)
        keys.extend(key)
        data.extend(content)

    if filename.endswith('.jsonl'):
        content,key = process_json_file(filename)
        keys.extend(key)
        data.extend(content)
        
    del content
    del key

/home/ubuntu/Datasets/Raw_Datasets/news/therakyatpost.com.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/sinar_harian_link_politik.json
/home/ubuntu/Datasets/Raw_Datasets/news/selangorkini.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/utusan-20230512.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/theedgemalaysia.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/themalaysianinsights.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/malaysiakini-bm.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/kosmo-20230524.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/parse-bernama.json
/home/ubuntu/Datasets/Raw_Datasets/news/sinar_harian_link_sukan.json
/home/ubuntu/Datasets/Raw_Datasets/news/melakahariini.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/fmt.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/theborneopost.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/sinar_harian_link_berita.json
/home/ubuntu/Datasets/Raw_Datasets/news/malaymail-02.jsonl
/home/ubuntu/Datasets/Raw_Datasets/news/malaymail-01.jsonl
/home/

In [62]:
len(data)

3046204

In [63]:
!free -h

               total        used        free      shared  buff/cache   available
Mem:           216Gi        33Gi        24Gi        86Mi       157Gi       180Gi
Swap:             0B          0B          0B


In [64]:
keys = list(set(keys))

In [65]:
keys

['reading_time',
 'tags',
 'p',
 'article_dt',
 'href',
 'text',
 'article_title',
 'author_name',
 'url',
 'content',
 'by',
 'article_text',
 'body',
 'index',
 'article_url',
 'headline',
 'title',
 'access_date',
 'h4']

In [66]:
content_keys = ['p','text','article_text','article_body','text','content','body','articleBody']

title_keys = ['headline','title','article_title']

In [67]:
news_data = []
rejected = []

for i, x in enumerate(data):
    
    try:
        text_key = [key for key in x.keys() if key in content_keys][0]
        
        title_key = [key for key in x.keys() if key in title_keys]
        
        title = ""
        if title_key:
            title_key = title_key[0] 
            if isinstance(x[title_key], str):
                title = x[title_key] + "\n" 
        
        if isinstance(x[text_key], str):
            text = title + x[text_key]
        elif isinstance(x[text_key], list):
            text = title + '\n'.join(x[text_key])
        else:
            continue
        
       
            
    except:
        rejected.append(x)
        print(x.keys())
        print(x)
        break
        

    news_data.append({'text': text})


In [68]:
len(news_data)

3036791

In [69]:
news_data[-1]

{'text': 'Medical specialist group urges govt to clarify vulnerable groups for Covid-19 vaccination\n KUALA LUMPUR, March 3 — The Academy of Medicine of Malaysia (AMM) has urged the government to clarify where high-risk groups fall on the priority list in the National Covid-19 Immunisation Programme.\n The medical specialist group in a statement today said the vaccine registration process in the MySejahtera app does little to inform pregnant women and immunosuppressed patients of their risk status.\n “It also falls short of providing resources for educating those with comorbidities on the Covid-19 vaccine as it relates to their condition.\n “We urge the government to provide necessary updates to the app that will allow patients to empower themselves with the information and resources to get vaccinated according to their risk group,” it said.\n AMM said the country’s immunisation strategy must be inclusive and empower high-risk, vulnerable groups with information to make good decisions.

In [70]:
data_dict = {
    'text': [entry['text'] for entry in news_data]

}

In [71]:
dataset = Dataset.from_dict(data_dict)

In [72]:
dataset

Dataset({
    features: ['text'],
    num_rows: 3036791
})

In [73]:
dataset.save_to_disk(f"hf-datasets/raw-datasets/news")

Saving the dataset (0/14 shards):   0%|          | 0/3036791 [00:00<?, ? examples/s]

In [76]:
command = f"python3 -m text_dedup.minhash \
  --path hf-datasets/raw-datasets/news \
  --split train \
  --cache_dir ./cache \
  --output hf-datasets/dedupe-datasets/news \
  --column text \
  --batch_size 10000 \
  --threshold 0.95 \
  --local \
  --min_length 1"

command

'python3 -m text_dedup.minhash   --path hf-datasets/raw-datasets/news   --split train   --cache_dir ./cache   --output hf-datasets/dedupe-datasets/news   --column text   --batch_size 10000   --threshold 0.95   --local   --min_length 1'

In [77]:
import subprocess
subprocess.run(command, shell=True)

Clustering...: 100%|██████████| 5/5 [00:02<00:00,  2.19it/s]


Duplicate pairs before filtering:
Cluster 416 has duplicate pairs: [416, 7039]
Cluster 488 has duplicate pairs: [488, 6716]
Cluster 615 has duplicate pairs: [615, 3862]
Cluster 835 has duplicate pairs: [835, 7692]
Cluster 1022 has duplicate pairs: [1022, 3346]
Cluster 1032 has duplicate pairs: [1032, 4023]
Cluster 1224 has duplicate pairs: [1224, 2793]
Cluster 1490 has duplicate pairs: [1490, 2800]
Cluster 1721 has duplicate pairs: [1721, 5039]
Cluster 1901 has duplicate pairs: [1901, 3647]
Cluster 1963 has duplicate pairs: [1963, 5829]
Cluster 1984 has duplicate pairs: [1984, 7957]
Cluster 2591 has duplicate pairs: [2591, 5092]
Cluster 2605 has duplicate pairs: [2605, 7836]
Cluster 2785 has duplicate pairs: [2785, 5948]
Cluster 2962 has duplicate pairs: [2962, 3548]
Cluster 3516 has duplicate pairs: [3516, 9757]
Cluster 3616 has duplicate pairs: [3616, 10201]
Cluster 3739 has duplicate pairs: [3739, 5262]
Cluster 3742 has duplicate pairs: [3742, 8914]
Cluster 3786 has duplicate pairs:

Cluster 67563 has duplicate pairs: [67563, 67591, 67621, 67652, 67680, 67714, 67737, 67765, 67792, 67823, 67852, 67884, 67911, 67939, 67968, 67998, 68026, 68056, 68086, 68114, 68144, 68173, 68201, 68230, 68261, 68286, 68319, 68347, 68375, 68404, 68437, 68464, 68492, 68518, 68547, 68579, 68606, 68635, 68665, 68696, 68725, 68752, 68782, 68811, 68839, 68867, 68897, 68925, 68953, 68983, 69013, 69043, 69070, 69099, 69128, 69158, 69189, 69215, 69244, 69273, 69302, 69331, 69363, 69393, 69421, 69446, 69476, 69506, 69536, 69563, 69592, 69622, 69650, 69679, 69711, 69743, 69765, 69795, 69824, 69853, 69882, 69909, 69942, 69968, 69997, 70029, 70059, 70084, 70117, 70146, 70174, 70202, 70232, 70261, 70288, 70318, 70345, 70377, 70404, 70435, 70463, 70491, 70520, 70550, 70580, 70608, 70636, 70667, 70695, 70725, 70752, 70781, 70812, 70841, 70868, 70897, 70926, 70954, 70983, 71014, 71046, 71070, 71103, 71128, 71161, 71190, 71217, 71245, 71278, 71303, 71336, 71362, 71392, 71421, 71450, 71481, 71507, 71539

Cluster 67564 has duplicate pairs: [67564, 67592, 67622, 67655, 67681, 67716, 67738, 67766, 67794, 67824, 67853, 67885, 67912, 67940, 67969, 67999, 68027, 68057, 68088, 68115, 68145, 68174, 68203, 68233, 68262, 68287, 68320, 68348, 68376, 68406, 68438, 68465, 68494, 68519, 68548, 68580, 68607, 68636, 68666, 68697, 68726, 68754, 68783, 68813, 68840, 68868, 68898, 68927, 68954, 68984, 69014, 69045, 69071, 69103, 69129, 69160, 69190, 69216, 69245, 69275, 69303, 69332, 69364, 69394, 69422, 69447, 69477, 69507, 69537, 69564, 69597, 69623, 69651, 69680, 69712, 69744, 69767, 69796, 69825, 69854, 69883, 69910, 69943, 69969, 69998, 70030, 70060, 70085, 70118, 70150, 70175, 70203, 70233, 70262, 70290, 70319, 70347, 70378, 70405, 70437, 70464, 70492, 70521, 70551, 70581, 70609, 70637, 70668, 70696, 70727, 70753, 70782, 70813, 70842, 70869, 70898, 70928, 70955, 70984, 71015, 71047, 71071, 71107, 71129, 71162, 71191, 71218, 71246, 71279, 71304, 71337, 71365, 71393, 71422, 71451, 71482, 71508, 71540

Cluster 67565 has duplicate pairs: [67565, 67593, 67623, 67653, 67682, 67715, 67739, 67767, 67795, 67826, 67854, 67886, 67913, 67941, 67970, 68000, 68028, 68058, 68089, 68116, 68146, 68175, 68202, 68232, 68263, 68288, 68323, 68351, 68378, 68407, 68436, 68466, 68493, 68520, 68549, 68581, 68608, 68637, 68667, 68698, 68727, 68755, 68784, 68814, 68841, 68869, 68899, 68928, 68956, 68985, 69015, 69046, 69072, 69102, 69131, 69161, 69191, 69217, 69246, 69276, 69307, 69333, 69365, 69395, 69423, 69449, 69479, 69508, 69538, 69565, 69596, 69624, 69652, 69681, 69713, 69746, 69768, 69797, 69826, 69855, 69886, 69911, 69944, 69972, 69999, 70031, 70061, 70086, 70119, 70149, 70176, 70205, 70234, 70263, 70291, 70320, 70348, 70380, 70406, 70436, 70465, 70494, 70523, 70553, 70586, 70610, 70638, 70669, 70698, 70726, 70754, 70783, 70814, 70844, 70870, 70899, 70929, 70956, 70985, 71017, 71048, 71073, 71106, 71131, 71163, 71192, 71219, 71248, 71281, 71305, 71338, 71364, 71394, 71423, 71452, 71483, 71509, 71541

...

Cluster 2475545 has duplicate pairs: [2475545, 2810071]
Cluster 2475644 has duplicate pairs: [2475644, 2475647]
Cluster 2475798 has duplicate pairs: [2475798, 2475799]
Cluster 2481039 has duplicate pairs: [2481039, 2481046]
Cluster 2481108 has duplicate pairs: [2481108, 2481112]
Cluster 2484653 has duplicate pairs: [2484653, 2487131, 2487304]
Cluster 2490160 has duplicate pairs: [2490160, 2490173]
Cluster 2492290 has duplicate pairs: [2492290, 2795591]
Cluster 2499245 has duplicate pairs: [2499245, 2499246]
Cluster 2499507 has duplicate pairs: [2499507, 2499508]
Cluster 2501298 has duplicate pairs: [2501298, 2781129]
Cluster 2502582 has duplicate pairs: [2502582, 2641331]
Cluster 2503111 has duplicate pairs: [2503111, 2503112, 2503113]
Cluster 2504499 has duplicate pairs: [2504499, 2504500]
Cluster 2504695 has duplicate pairs: [2504695, 2504696]
Cluster 2505712 has duplicate pairs: [2505712, 2505713]
Cluster 2505794 has duplicate pairs: [2505794, 2505795]
Cluster 2506969 has duplicate 

Cluster 2767036 has duplicate pairs: [2767036, 2767037]
Cluster 2767038 has duplicate pairs: [2767038, 2767039]
Cluster 2767040 has duplicate pairs: [2767040, 2767041]
Cluster 2767042 has duplicate pairs: [2767042, 2767043]
Cluster 2767044 has duplicate pairs: [2767044, 2767045]
Cluster 2767046 has duplicate pairs: [2767046, 2767047]
Cluster 2767048 has duplicate pairs: [2767048, 2767049]
Cluster 2767050 has duplicate pairs: [2767050, 2767051]
Cluster 2767052 has duplicate pairs: [2767052, 2767053]
Cluster 2767054 has duplicate pairs: [2767054, 2767055]
Cluster 2770289 has duplicate pairs: [2770289, 2770720]
Cluster 2770323 has duplicate pairs: [2770323, 2770721]
Cluster 2770534 has duplicate pairs: [2770534, 2770537]
Cluster 2770540 has duplicate pairs: [2770540, 2770549]
Cluster 2770637 has duplicate pairs: [2770637, 2770770]
Cluster 2770671 has duplicate pairs: [2770671, 2770673]
Cluster 2770679 has duplicate pairs: [2770679, 2770794]
Cluster 2770688 has duplicate pairs: [2770688, 2

Creating json from Arrow format: 100%|██████████| 2840/2840 [01:06<00:00, 43.02ba/s]                      


[08/17/23 06:00:57] INFO     Loading                         :    ]8;id=783334;file:///home/ubuntu/aisyah/text_dedup/minhash.py\minhash.py]8;;\:]8;id=835856;file:///home/ubuntu/aisyah/text_dedup/minhash.py#336\336]8;;\
                             0.05s                                              
                    INFO     MinHashing                      :    ]8;id=189680;file:///home/ubuntu/aisyah/text_dedup/minhash.py\minhash.py]8;;\:]8;id=725959;file:///home/ubuntu/aisyah/text_dedup/minhash.py#336\336]8;;\
                             277.32s                                            
                    INFO     Clustering                      :    ]8;id=299283;file:///home/ubuntu/aisyah/text_dedup/minhash.py\minhash.py]8;;\:]8;id=530820;file:///home/ubuntu/aisyah/text_dedup/minhash.py#336\336]8;;\
                             44.59s                                             
                    INFO     Filtering                       :    ]8;id=427

CompletedProcess(args='python3 -m text_dedup.minhash   --path hf-datasets/raw-datasets/news   --split train   --cache_dir ./cache   --output hf-datasets/dedupe-datasets/news   --column text   --batch_size 10000   --threshold 0.95   --local   --min_length 1', returncode=0)

In [2]:
import json

with open(f'/home/ubuntu/aisyah/hf-datasets/dedupe-datasets/news/duplicates_cluster.jsonl') as file:
    data = [json.loads(line) for line in file]

filtered_list = []
for i,d in enumerate(data):
    if d['__cluster__'] == 2383830:
        filtered_list.append(d)

print(filtered_list[0])

{'text': 'Kane dakwa pengadil gagal tangani insiden Welbeck\nKAPTEN England, Harry Kane, mengecam pengadil, Danny Makkelie, setelah gagal mengawal tekanan sehingga menafikan jaringan Danny Welbeck, sekali gus menyebabkan pasukannya tewas 2-1 di tangan Sepanyol dalam saingan Liga Negara-Negara UEFA, awal pagi tadi.\n\r\nWelbeck menjaringkan gol dalam waktu kecederaan ketika England cuba untuk mengikat kedudukan di Wembley selepas gol daripada Saul Niguez dan Rodrigo dalam babak pertama meletakkan Sepanyol di depan.\n\r\nGol pembukaan Marcus Rashford memberikan sinar buat England tetapi mereka bergelut untuk menyaingi Sepanyol sehingga 20 minit terakhir di mana mereka cuba mendapatkan jaringan penyamaan.\n\r\nDitanya sama ada gol Welbeck itu patut dikira selepas kekasaran terhadap David De Gea, Kane memberitahu Sky Sports: "100 peratus.\n\r\n"Dalam detik yang besar sebegitu, anda memerlukan pengadil yang tetap pendirian tetapi dia merosakkannya.\n\r\n"Anda memerlukan pengadil yang teguh 

In [3]:
print(filtered_list[1])

{'text': 'Kane dakwa pengadil gagal tangani insiden Welbeck\nKAPTEN England, Harry Kane, mengecam pengadil, Danny Makkelie, setelah gagal mengawal tekanan sehingga menafikan jaringan Danny Welbeck, sekali gus menyebabkan pasukannya tewas 2-1 di tangan Sepanyol dalam saingan Liga Negara-Negara UEFA, awal pagi tadi.\n\r\nWelbeck menjaringkan gol dalam waktu kecederaan ketika England cuba untuk mengikat kedudukan di Wembley selepas gol daripada Saul Niguez dan Rodrigo dalam babak pertama meletakkan Sepanyol di depan.\n\r\nGol pembukaan Marcus Rashford memberikan sinar buat England tetapi mereka bergelut untuk menyaingi Sepanyol sehingga 20 minit terakhir di mana mereka cuba mendapatkan jaringan penyamaan.\n\r\nDitanya sama ada gol Welbeck itu patut dikira selepas kekasaran terhadap David De Gea, Kane memberitahu Sky Sports: "100 peratus.\n\r\n"Dalam detik yang besar sebegitu, anda memerlukan pengadil yang tetap pendirian tetapi dia merosakkannya.\n\r\n"Anda memerlukan pengadil yang teguh 

In [5]:
print(filtered_list[-1])

{'text': 'Kane dakwa pengadil gagal tangani insiden Welbeck\nKAPTEN England, Harry Kane, mengecam pengadil, Danny Makkelie, setelah gagal mengawal tekanan sehingga menafikan jaringan Danny Welbeck, sekali gus menyebabkan pasukannya tewas 2-1 di tangan Sepanyol dalam saingan Liga Negara-Negara UEFA, awal pagi tadi.\n\r\nWelbeck menjaringkan gol dalam waktu kecederaan ketika England cuba untuk mengikat kedudukan di Wembley selepas gol daripada Saul Niguez dan Rodrigo dalam babak pertama meletakkan Sepanyol di depan.\n\r\nGol pembukaan Marcus Rashford memberikan sinar buat England tetapi mereka bergelut untuk menyaingi Sepanyol sehingga 20 minit terakhir di mana mereka cuba mendapatkan jaringan penyamaan.\n\r\nDitanya sama ada gol Welbeck itu patut dikira selepas kekasaran terhadap David De Gea, Kane memberitahu Sky Sports: "100 peratus.\n\r\n"Dalam detik yang besar sebegitu, anda memerlukan pengadil yang tetap pendirian tetapi dia merosakkannya.\n\r\n"Anda memerlukan pengadil yang teguh 

In [20]:
filtered_list = []
for i,d in enumerate(data):
    if d['__cluster__'] == 67580:
        filtered_list.append(d)

print(filtered_list[0])

{'text': 'Ancaman strok haba, kekhuatiran Covid-19 berulang\nOleh Meor Harman Meor Shakri\n\n\n3 Mei 2023, 7:44 am\nJADUAL persekolahan kembali bersambung semalam selepas lebih seminggu menikmati cuti Hari Raya Aidilfitri. Di sebalik keseronokan itu, ramai yang bimbang dengan keadaan cuaca panas yang melanda negara sejak Ramadan dan penularan Covid-19 selepas asyik beraya. Kes melibatkan strok haba sudah mula didengari, malah kenaikan kes jangkitan Covid-19 juga menunjukkan ada peningkatan. Di Kedah, laporan sebelum ini menyebut 281 kes baharu…\n\xa0\n\xa0\nSila Log Masuk atau Langgan untuk membaca berita sepenuhnya', '__cluster__': 67580}


In [21]:
filtered_list[2000]

{'text': 'Ancaman strok haba, kekhuatiran Covid-19 berulang\nOleh Meor Harman Meor Shakri\n\n\n3 Mei 2023, 7:44 am\nJADUAL persekolahan kembali bersambung semalam selepas lebih seminggu menikmati cuti Hari Raya Aidilfitri. Di sebalik keseronokan itu, ramai yang bimbang dengan keadaan cuaca panas yang melanda negara sejak Ramadan dan penularan Covid-19 selepas asyik beraya. Kes melibatkan strok haba sudah mula didengari, malah kenaikan kes jangkitan Covid-19 juga menunjukkan ada peningkatan. Di Kedah, laporan sebelum ini menyebut 281 kes baharu…\n\xa0\n\xa0\nSila Log Masuk atau Langgan untuk membaca berita sepenuhnya',
 '__cluster__': 67580}